In [47]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
import matplotlib.pyplot as plt

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library
from sklearn.metrics import silhouette_score

import seaborn as sns


print('Libraries imported.')

Libraries imported.


### Getting the New York Neighborhood data into a DataFrame

In [48]:
neighborhoods = pd.read_csv("data.csv")

In [49]:
neighborhoods.drop(columns="Unnamed: 0", inplace = True)
neighborhoods.shape

(306, 4)

In [50]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


### Creating a map of New York along with it's neighborhoods superimposed on the map

In [52]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [53]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [54]:
neighborhoods
#neighborhoods_broman = neighborhoods.loc[(neighborhoods['Borough'] == 'Brooklyn')|(neighborhoods['Borough'] == 'Manhattan')]
#neighborhoods_broman = neighborhoods_broman.reset_index(drop=True)
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [55]:
neighborhoods.shape

(306, 4)

### Using foursquare location data

In [56]:
CLIENT_ID = 'OLN1BAQQBHO234LKFIU1ZNGV4Z3O3P1GS5KIMTNPJHLX1MKL' # your Foursquare ID
CLIENT_SECRET = 'VDM5CGGVSUOGKMY21ETO4J1UAJH5QJEALQCJAIWUF2DJXR2T' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: OLN1BAQQBHO234LKFIU1ZNGV4Z3O3P1GS5KIMTNPJHLX1MKL
CLIENT_SECRET:VDM5CGGVSUOGKMY21ETO4J1UAJH5QJEALQCJAIWUF2DJXR2T


### Exploring the venues in the neighborhoods of New York 

In [57]:
def getNearbyVenues(names, latitudes, longitudes, LIMIT=200, radius=1000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)


### Run the above function on each neighborhood and create a new dataframe called venues.



In [58]:
venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                  latitudes=neighborhoods['Latitude'],
                                  longitudes=neighborhoods['Longitude'],
                                  LIMIT=200)

print('The "venues" dataframe has {} venues and {} unique venue types.'.format(
      len(venues['Venue Category']),
      len(venues['Venue Category'].unique())))

venues.to_csv('venues.csv', sep=',', encoding='UTF8')
venues.head()

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

SSLError: HTTPSConnectionPool(host='api.foursquare.com', port=443): Max retries exceeded with url: /v2/venues/explore?&client_id=OLN1BAQQBHO234LKFIU1ZNGV4Z3O3P1GS5KIMTNPJHLX1MKL&client_secret=VDM5CGGVSUOGKMY21ETO4J1UAJH5QJEALQCJAIWUF2DJXR2T&v=20180605&ll=40.61305976667942,-73.96836678035541&radius=1000&limit=200 (Caused by SSLError(SSLError("bad handshake: SysCallError(10054, 'WSAECONNRESET')",),))

In [59]:
colnames = ['Neighborhood', 'Neighborhood Latitude', 'Neighborhood Longitude', 'Venue', 'Venue Latitude', 'Venue Longitude', 'Venue Category']
venues = pd.read_csv('venues.csv', skiprows=1, names=colnames)
venues.columns = venues.columns.str.replace(' ', '')
venues.head()

Neighborhood  NeighborhoodLatitude  NeighborhoodLongitude  \
0    Wakefield             40.894705             -73.847201   
1    Wakefield             40.894705             -73.847201   
2    Wakefield             40.894705             -73.847201   
3    Wakefield             40.894705             -73.847201   
4    Wakefield             40.894705             -73.847201   

                         Venue  VenueLatitude  VenueLongitude  \
0             Lollipops Gelato      40.894123      -73.845892   
1           Ripe Kitchen & Bar      40.898152      -73.838875   
2              Ali's Roti Shop      40.894036      -73.856935   
3                     Rite Aid      40.896649      -73.844846   
4  Jackie's West Indian Bakery      40.889283      -73.843310   

          VenueCategory  
0          Dessert Shop  
1  Caribbean Restaurant  
2  Caribbean Restaurant  
3              Pharmacy  
4  Caribbean Restaurant

In [60]:
def Venues_Map(Borough_name, Borough_neighborhoods):
    
    # Use geopy library to get the latitude and longitude values 
    geolocator = Nominatim(user_agent="Jupyter")
    Borough_location = geolocator.geocode(Borough_name) #'Brooklyn, NY'
    Borough_latitude = Borough_location.latitude
    Borough_longitude = Borough_location.longitude
    print('The geographical coordinates of "{}" are {}, {}.'.format(Borough_name, Borough_latitude, Borough_longitude))
    
    # To verify the number of Boroughs and Neighborhoods in the extracted data
    print('The "{}" dataframe has {} different venue types and {} neighborhoods.'.format(
          Borough_name,
          len(Borough_neighborhoods['VenueCategory'].unique()),
          len(Borough_neighborhoods['Neighborhood'].unique())))
    
    # create map of city using latitude and longitude values
    map_Borough = folium.Map(location=[Borough_latitude, Borough_longitude], zoom_start=10)

    # add markers to map
    for lat, lng, venue, category in zip(Borough_neighborhoods['VenueLatitude'], Borough_neighborhoods['VenueLongitude'], Borough_neighborhoods['Venue'], Borough_neighborhoods['VenueCategory']):
        label = '{}, {}'.format(category, venue)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=0.1,
            popup=label,
            color='red',
            fill=True,
            fill_color='#FF0000',
            fill_opacity=0.3).add_to(map_Borough)  

    return map_Borough

In [61]:
Venues_Map('New York City, NY', venues)

GeocoderTimedOut: Service timed out

In [62]:
venues.groupby('VenueCategory')['Venue'].count().sort_values(ascending=False)

VenueCategory
Pizza Place                                 1029
Italian Restaurant                           544
Coffee Shop                                  521
Deli / Bodega                                500
Donut Shop                                   435
Sandwich Place                               424
Bakery                                       423
Chinese Restaurant                           416
Bar                                          411
Pharmacy                                     409
Park                                         406
Grocery Store                                360
Ice Cream Shop                               338
Mexican Restaurant                           326
Café                                         319
Bank                                         316
American Restaurant                          313
Supermarket                                  299
Fast Food Restaurant                         281
Gym                                          257
Caribb

In [63]:
venues.groupby('Neighborhood').count()


NeighborhoodLatitude  NeighborhoodLongitude  Venue  \
Neighborhood                                                                    
Allerton                                     64                     64     64   
Annadale                                     17                     17     17   
Arden Heights                                19                     19     19   
Arlington                                    21                     21     21   
Arrochar                                     24                     24     24   
Arverne                                      37                     37     37   
Astoria                                     100                    100    100   
Astoria Heights                              78                     78     78   
Auburndale                                  100                    100    100   
Bath Beach                                   96                     96     96   
Battery Park City                           100                    100    100   
Bay Ridge                                   100                    100    100   
Bay Terrace                                 100                    100    100   
Baychester                                  100                    100    100   
Bayside                                     100                    100    100   
Bayswater                                     8                      8      8   
Bedford Park                                 78                     78     78   
Bedford Stuyvesant                          100                    100    100   
Beechhurst                                   56                     56     56   
Bellaire                                     56                     56     56   
Belle Harbor                                 28                     28     28   
Bellerose                                    52                     52     52   
Belmont                                     100                    100    100   
Bensonhurst                                 100                    100    100   
Bergen Beach                                  9                      9      9   
Blissville                                   69                     69     69   
Bloomfield                                   27                     27     27   
Boerum Hill                                 100                    100    100   
Borough Park                                 48                     48     48   
Breezy Point                                  5                      5      5   
Briarwood                                    87                     87     87   
Brighton Beach                               96                     96     96   
Broad Channel                                13                     13     13   
Broadway Junction                            54                     54     54   
Bronxdale                                   100                    100    100   
Brooklyn Heights                            100                    100    100   
Brookville                                   17                     17     17   
Brownsville                                  77                     77     77   
Bulls Head                                   56                     56     56   
Bushwick                                    100                    100    100   
Butler Manor                                  9                      9      9   
Cambria Heights                              31                     31     31   
Canarsie                                     34                     34     34   
Carnegie Hill                               100                    100    100   
Carroll Gardens                             100                    100    100   
Castle Hill                                  41                     41     41   
Castleton Corners                            53                     53     53   
Central Harlem                              100           

In [64]:
print('There are {} uniques categories.'.format(len(venues['VenueCategory'].unique())))


There are 473 uniques categories.


### Analyze Each Neighborhood


In [65]:
# one hot encoding
BM_onehot = pd.get_dummies(venues[['VenueCategory']], prefix="", prefix_sep="")

#column lists before adding neighborhood
column_names = ['Neighborhood'] + list(BM_onehot.columns)

# add neighborhood column back to dataframe
BM_onehot['Neighborhood'] = venues['Neighborhood'] 

# move neighborhood column to the first column
BM_onehot = BM_onehot[column_names]

BM_onehot.head()

Neighborhood  ATM  Accessories Store  Adult Boutique  Afghan Restaurant  \
0    Wakefield    0                  0               0                  0   
1    Wakefield    0                  0               0                  0   
2    Wakefield    0                  0               0                  0   
3    Wakefield    0                  0               0                  0   
4    Wakefield    0                  0               0                  0   

   African Restaurant  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Animal Shelter  Antique Shop  Aquarium  Arcade  \
0                    0               0             0         0       0   
1                    0               0             0         0       0   
2                    0               0             0         0       0   
3                    0               0             0         0       0   
4                    0               0             0         0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Dealership  Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  \
0                0            0              0                0          0   
1                0            0              0                0          0   
2                0            0              0                0          0   
3                0            0              0                0          0   
4                0            0              0                0          0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Basketball Stadium  Bath House  Beach  Beach Bar  \
0                 0                   0           0      0          0   
1                 0                   0           0      0          0   
2                 0                   0           0      0          0   
3                 0                   0           0      0          0   
4                 0                   0           0      0       

In [66]:
restaurant_List = []
search = 'Restaurant'
for i in BM_onehot.columns :
    if search in i:
        restaurant_List.append(i)

In [67]:
restaurant_List

['Afghan Restaurant',
 'African Restaurant',
 'American Restaurant',
 'Arepa Restaurant',
 'Argentinian Restaurant',
 'Asian Restaurant',
 'Australian Restaurant',
 'Austrian Restaurant',
 'Brazilian Restaurant',
 'Burmese Restaurant',
 'Cajun / Creole Restaurant',
 'Cambodian Restaurant',
 'Cantonese Restaurant',
 'Caribbean Restaurant',
 'Caucasian Restaurant',
 'Chinese Restaurant',
 'Colombian Restaurant',
 'Comfort Food Restaurant',
 'Cuban Restaurant',
 'Czech Restaurant',
 'Dim Sum Restaurant',
 'Dumpling Restaurant',
 'Eastern European Restaurant',
 'Egyptian Restaurant',
 'Empanada Restaurant',
 'English Restaurant',
 'Ethiopian Restaurant',
 'Falafel Restaurant',
 'Fast Food Restaurant',
 'Filipino Restaurant',
 'French Restaurant',
 'German Restaurant',
 'Gluten-free Restaurant',
 'Greek Restaurant',
 'Halal Restaurant',
 'Hawaiian Restaurant',
 'Himalayan Restaurant',
 'Hotpot Restaurant',
 'Indian Restaurant',
 'Indonesian Restaurant',
 'Israeli Restaurant',
 'Italian Rest

In [68]:
col_name = []
col_name = ['Neighborhood'] + restaurant_List
BM_restaurant = BM_onehot[col_name]
BM_restaurant = BM_restaurant.iloc[:,1::]


In [69]:
BM_restaurant_grouped = BM_restaurant.groupby('Neighborhood').sum().reset_index()
BM_restaurant_grouped

Neighborhood  Afghan Restaurant  African Restaurant  \
0                     Allerton                  0                   0   
1                     Annadale                  0                   0   
2                Arden Heights                  0                   0   
3                    Arlington                  0                   0   
4                     Arrochar                  0                   0   
5                      Arverne                  0                   0   
6                      Astoria                  0                   0   
7              Astoria Heights                  0                   0   
8                   Auburndale                  0                   0   
9                   Bath Beach                  0                   0   
10           Battery Park City                  0                   0   
11                   Bay Ridge                  0                   0   
12                 Bay Terrace                  0                   0   
13                  Baychester                  0                   0   
14                     Bayside                  0                   0   
15                   Bayswater                  0                   0   
16                Bedford Park                  0                   0   
17          Bedford Stuyvesant                  0                   0   
18                  Beechhurst                  0                   0   
19                    Bellaire                  0                   0   
20                Belle Harbor                  0                   0   
21                   Bellerose                  0                   0   
22                     Belmont                  0                   1   
23                 Bensonhurst                  0                   0   
24                Bergen Beach                  0                   0   
25                  Blissville                  0                   0   
26                  Bloomfield                  0                   0   
27                 Boerum Hill                  0                   0   
28                Borough Park                  0                   0   
29                Breezy Point                  0                   0   
30                   Briarwood                  0                   0   
31              Brighton Beach                  0                   0   
32               Broad Channel                  0                   0   
33           Broadway Junction                  0                   0   
34                   Bronxdale                  0                   0   
35            Brooklyn Heights                  0                   0   
36                  Brookville                  0                   0   
37                 Brownsville                  0                   0   
38                  Bulls Head                  0                   0   
39                    Bushwick                  0                   0   
40                Butler Manor                  0                   0   
41             Cambria Heights                  0                   0   
42                    Canarsie                  0                   0   
43               Carnegie Hill                  0                   0   
44             Carroll Gardens                  0                   0   
45                 Castle Hill                  0                   0   
46           Castleton Corners                  0                   0   
47              Central Harlem                  0                   4   
48                  Charleston                  0                   0   
49                     Chelsea                  0                   0   
50                   Chinatown                  0                   0   
51                 City Island                  0                   0   
52                   City Line                  0                   0   
53                Civic Center                  0                   0   
54 

In [70]:
BM_restaurant_grouped['Total'] = BM_restaurant_grouped .sum(axis=1)
BM_restaurant_grouped

Neighborhood  Afghan Restaurant  African Restaurant  \
0                     Allerton                  0                   0   
1                     Annadale                  0                   0   
2                Arden Heights                  0                   0   
3                    Arlington                  0                   0   
4                     Arrochar                  0                   0   
5                      Arverne                  0                   0   
6                      Astoria                  0                   0   
7              Astoria Heights                  0                   0   
8                   Auburndale                  0                   0   
9                   Bath Beach                  0                   0   
10           Battery Park City                  0                   0   
11                   Bay Ridge                  0                   0   
12                 Bay Terrace                  0                   0   
13                  Baychester                  0                   0   
14                     Bayside                  0                   0   
15                   Bayswater                  0                   0   
16                Bedford Park                  0                   0   
17          Bedford Stuyvesant                  0                   0   
18                  Beechhurst                  0                   0   
19                    Bellaire                  0                   0   
20                Belle Harbor                  0                   0   
21                   Bellerose                  0                   0   
22                     Belmont                  0                   1   
23                 Bensonhurst                  0                   0   
24                Bergen Beach                  0                   0   
25                  Blissville                  0                   0   
26                  Bloomfield                  0                   0   
27                 Boerum Hill                  0                   0   
28                Borough Park                  0                   0   
29                Breezy Point                  0                   0   
30                   Briarwood                  0                   0   
31              Brighton Beach                  0                   0   
32               Broad Channel                  0                   0   
33           Broadway Junction                  0                   0   
34                   Bronxdale                  0                   0   
35            Brooklyn Heights                  0                   0   
36                  Brookville                  0                   0   
37                 Brownsville                  0                   0   
38                  Bulls Head                  0                   0   
39                    Bushwick                  0                   0   
40                Butler Manor                  0                   0   
41             Cambria Heights                  0                   0   
42                    Canarsie                  0                   0   
43               Carnegie Hill                  0                   0   
44             Carroll Gardens                  0                   0   
45                 Castle Hill                  0                   0   
46           Castleton Corners                  0                   0   
47              Central Harlem                  0                   4   
48                  Charleston                  0                   0   
49                     Chelsea                  0                   0   
50                   Chinatown                  0                   0   
51                 City Island                  0                   0   
52                   City Line                  0                   0   
53                Civic Center                  0                   0   
54 

###  Cluster Neighborhoods and Examine Clusters
First, let's determine the optimal value of K for our dataset using the Silhouette Coefficient Method



In [71]:
BM_grouped_clustering = BM_restaurant_grouped.drop('Neighborhood', 1)

for n_cluster in range(2, 10):
    kmeans = KMeans(n_clusters=n_cluster).fit(BM_grouped_clustering)
    label = kmeans.labels_
    sil_coeff = silhouette_score(BM_grouped_clustering, label, metric='euclidean')
    print("For n_clusters={}, The Silhouette Coefficient is {}".format(n_cluster, sil_coeff))


For n_clusters=2, The Silhouette Coefficient is 0.4791865828429841
For n_clusters=3, The Silhouette Coefficient is 0.37747915696786427
For n_clusters=4, The Silhouette Coefficient is 0.3698738389962575
For n_clusters=5, The Silhouette Coefficient is 0.29449748379612256
For n_clusters=6, The Silhouette Coefficient is 0.3065011700489024
For n_clusters=7, The Silhouette Coefficient is 0.25433174172007256
For n_clusters=8, The Silhouette Coefficient is 0.2113810648693998
For n_clusters=9, The Silhouette Coefficient is 0.1964642884048377


##### As we can see, n_clusters=2 has highest Silhouette Coefficient. This means that 2 should be the optimal number of clusters.

In [72]:

# set number of clusters
kclusters = 2

BM_grouped_clustering = BM_restaurant_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(BM_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_


array([0, 0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0,
       1, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1,
       1, 0, 0, 1, 0, 1, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0,
       1, 0, 1, 0, 1, 1, 1, 1, 0, 1, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0, 0, 0,
       1, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0,
       0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0,
       1, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 0, 1, 0, 0, 1, 1, 0, 0,
       0, 1, 1, 0, 0, 1, 0, 0, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1,
       0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1, 1, 0, 1, 0,
       0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1,
       1, 0, 1, 0, 0, 1, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0,
       0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 1,
       1, 1, 1, 1, 0, 0, 0, 0, 0, 1, 1, 1, 1, 0, 1, 1, 0, 0, 0, 0, 1, 1,
       0, 0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1,

In [73]:

BM_results = pd.DataFrame(kmeans.cluster_centers_)
BM_results.columns = BM_grouped_clustering.columns
BM_results.index = ['cluster0','cluster1']
BM_results['Total Sum'] = BM_results.sum(axis = 1)
BM_results

Afghan Restaurant  African Restaurant  American Restaurant  \
cluster0           0.010204            0.030612             0.678571   
cluster1           0.009434            0.075472             1.698113   

          Arepa Restaurant  Argentinian Restaurant  Asian Restaurant  \
cluster0          0.025510                0.005102          0.224490   
cluster1          0.122642                0.169811          0.707547   

          Australian Restaurant  Austrian Restaurant  Brazilian Restaurant  \
cluster0           4.857226e-17         6.591949e-17              0.020408   
cluster1           9.433962e-02         6.603774e-02              0.103774   

          Burmese Restaurant  Cajun / Creole Restaurant  Cambodian Restaurant  \
cluster0       -8.239937e-18                   0.015306          1.734723e-17   
cluster1        9.433962e-03                   0.113208          2.830189e-02   

          Cantonese Restaurant  Caribbean Restaurant  Caucasian Restaurant  \
cluster0              0.010204              0.790816              0.005102   
cluster1              0.132075              0.905660              0.037736   

          Chinese Restaurant  Colombian Restaurant  Comfort Food Restaurant  \
cluster0            1.198980              0.010204                 0.015306   
cluster1            1.707547              0.047170                 0.075472   

          Cuban Restaurant  Czech Restaurant  Dim Sum Restaurant  \
cluster0          0.030612      1.734723e-17            0.005102   
cluster1          0.235849      2.830189e-02            0.066038   

          Dumpling Restaurant  Eastern European Restaurant  \
cluster0             0.020408                     0.056122   
cluster1             0.141509                     0.169811   

          Egyptian Restaurant  Empanada Restaurant  English Restaurant  \
cluster0        -8.239937e-18             0.005102       -1.647987e-17   
cluster1         9.433962e-03             0.084906        1.886792e-02   

          Ethiopian Restaurant  Falafel Restaurant  Fast Food Restaurant  \
cluster0          6.938894e-17            0.025510              1.096939   
cluster1          1.132075e-01            0.122642              0.622642   

          Filipino Restaurant  French Restaurant  German Restaurant  \
cluster0             0.020408           0.056122           0.040816   
cluster1             0.150943           0.811321           0.084906   

          Gluten-free Restaurant  Greek Restaurant  Halal Restaurant  \
cluster0            5.102041e-03          0.071429          0.015306   
cluster1           -1.734723e-18          0.641509          0.075472   

          Hawaiian Restaurant  Himalayan Restaurant  Hotpot Restaurant  \
cluster0             0.005102          3.469447e-17      -6.591949e-17   
cluster1             0.047170          5.660377e-02       7.547170e-02   

          Indian Restaurant  Indonesian Restaurant  Israeli Restaurant  \
cluster0           0.209184          -3.295975e-17       -3.295975e-17   
cluster1           0.981132           3.773585e-02        3.773585e-02   

          Italian Restaurant  Japanese Curry Restaurant  Japanese Restaurant  \
cluster0            1.209184                   0.015306             0.301020   
cluster1            2.896226                   0.037736             1.292453   

          Jewish Restaurant  Kebab Restaurant  Korean Restaurant  \
cluster0       1.734723e-17     -1.647987e-17           0.040816   
cluster1       2.830189e-02      1.886792e-02           0.962264   

          Kosher Restaurant  Latin American Restaurant  Lebanese Restaurant  \
cluster0       2.428613e-17                   0.316327         3.469447e-17   
cluster1       4.716981e-02                   1.113208         5.660377e-02   

          Malay Restaurant  Mediterranean Restaurant  Mexican Restaurant  \
cluster0     -3.816392e-17                  0.107143            0.581633   
cluster1      8.490566e-02                  0.490566            2.0

The Total and Total Sum of cluster0 has smallest value. It shows that the market is not saturated.



#### Dataframe with Neighborhood,Cluster No and Total Sum



In [74]:
BM_results_merged = pd.DataFrame(BM_restaurant_grouped['Neighborhood'])

BM_results_merged['Total'] = BM_restaurant_grouped['Total']
BM_results_merged = BM_results_merged.assign(Cluster_Labels = kmeans.labels_)


In [75]:
print(BM_results_merged.shape)
BM_results_merged

(302, 3)


Neighborhood  Total  Cluster_Labels
0                     Allerton     15               0
1                     Annadale      2               0
2                Arden Heights      4               0
3                    Arlington      3               0
4                     Arrochar      4               0
5                      Arverne      4               0
6                      Astoria     29               1
7              Astoria Heights      8               0
8                   Auburndale     34               1
9                   Bath Beach     33               1
10           Battery Park City      7               0
11                   Bay Ridge     34               1
12                 Bay Terrace     17               0
13                  Baychester     14               0
14                     Bayside     32               1
15                   Bayswater      1               0
16                Bedford Park     11               0
17          Bedford Stuyvesant     22               1
18                  Beechhurst     10               0
19                    Bellaire     11               0
20                Belle Harbor      3               0
21                   Bellerose      5               0
22                     Belmont     25               1
23                 Bensonhurst     28               1
24                Bergen Beach      2               0
25                  Blissville     15               0
26                  Bloomfield      0               0
27                 Boerum Hill     18               0
28                Borough Park      6               0
29                Breezy Point      1               0
30                   Briarwood     26               1
31              Brighton Beach     21               1
32               Broad Channel      1               0
33           Broadway Junction      8               0
34                   Bronxdale     16               0
35            Brooklyn Heights     23               1
36                  Brookville      3               0
37                 Brownsville     11               0
38                  Bulls Head     11               0
39                    Bushwick     26               1
40                Butler Manor      1               0
41             Cambria Heights      6               0
42                    Canarsie      7               0
43               Carnegie Hill     21               1
44             Carroll Gardens     20               1
45                 Castle Hill      5               0
46           Castleton Corners      9               0
47              Central Harlem     36               1
48                  Charleston      9               0
49                     Chelsea     23               1
50                   Chinatown     28               1
51                 City Island     14               0
52                   City Line     15               0
53                Civic Center     24               1
54           Claremont Village      2               0
55                Clason Point      0               0
56                     Clifton     11               0
57                     Clinton     19               0
58                Clinton Hill     36               1
59                  Co-op City     15               0
60                 Cobble Hill     23               1
61               College Point     13               0
62                     Concord     10               0
63                   Concourse     14               0
64           Concourse Village     19               0
65                Coney Island      5               0
66                      Corona     21               1
67                Country Club     15               0
68               Crown Heights     20               1
69               Cypress Hills     10               0
70                 Ditmas Park     33               1
71                Dongan Hills     22               1
72                  Douglaston     26               1
73                    

In [76]:
BM_merged = neighborhoods

BM_merged = BM_merged.join(BM_results_merged.set_index('Neighborhood'), on='Neighborhood')

print(BM_merged.shape)
BM_merged.head(10) # check the last columns!
#BM_merged.groupby("Cluster_Labels").count()

(306, 6)


Borough    Neighborhood   Latitude  Longitude  Total  Cluster_Labels
0      Bronx       Wakefield  40.894705 -73.847201     12               0
1      Bronx      Co-op City  40.874294 -73.829939     15               0
2      Bronx     Eastchester  40.887556 -73.827806     13               0
3      Bronx       Fieldston  40.895437 -73.905643      6               0
4      Bronx       Riverdale  40.890834 -73.912585     10               0
5      Bronx     Kingsbridge  40.881687 -73.902818     21               1
6  Manhattan     Marble Hill  40.876551 -73.910660     13               0
7      Bronx        Woodlawn  40.898273 -73.867315      6               0
8      Bronx         Norwood  40.877224 -73.879391     14               0
9      Bronx  Williamsbridge  40.881039 -73.857446     15               0

#### Creating a visulization of the clusters

In [77]:

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(BM_merged['Latitude'], BM_merged['Longitude'], BM_merged['Neighborhood'], BM_merged['Cluster_Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Cluster 1 : Saturated Markets

In [78]:
BM_merged[BM_merged['Cluster_Labels'] == 1].reset_index(drop=True)


Borough               Neighborhood   Latitude  Longitude  Total  \
0            Bronx                Kingsbridge  40.881687 -73.902818     21   
1            Bronx                    Fordham  40.860997 -73.896427     24   
2            Bronx                Parkchester  40.837938 -73.856003     27   
3            Bronx                    Belmont  40.857277 -73.888452     25   
4            Bronx                  Unionport  40.829774 -73.850535     22   
5         Brooklyn                  Bay Ridge  40.625801 -74.030621     34   
6         Brooklyn                Bensonhurst  40.611009 -73.995180     28   
7         Brooklyn                Sunset Park  40.645103 -74.010316     39   
8         Brooklyn                 Greenpoint  40.730201 -73.954241     23   
9         Brooklyn             Brighton Beach  40.576825 -73.965094     21   
10        Brooklyn             Sheepshead Bay  40.586890 -73.943186     31   
11        Brooklyn          Manhattan Terrace  40.614433 -73.957438     20   
12        Brooklyn                   Flatbush  40.636326 -73.958401     33   
13        Brooklyn              Crown Heights  40.670829 -73.943291     20   
14        Brooklyn                 Kensington  40.642382 -73.980421     23   
15        Brooklyn            Windsor Terrace  40.656946 -73.980073     22   
16        Brooklyn           Prospect Heights  40.676822 -73.964859     31   
17        Brooklyn               Williamsburg  40.707144 -73.958115     28   
18        Brooklyn                   Bushwick  40.698116 -73.925258     26   
19        Brooklyn         Bedford Stuyvesant  40.687232 -73.941785     22   
20        Brooklyn           Brooklyn Heights  40.695864 -73.993782     23   
21        Brooklyn                Cobble Hill  40.687920 -73.998561     23   
22        Brooklyn            Carroll Gardens  40.680540 -73.994654     20   
23        Brooklyn                    Gowanus  40.673931 -73.994441     22   
24        Brooklyn                Fort Greene  40.688527 -73.972906     28   
25        Brooklyn                 Park Slope  40.672321 -73.977050     23   
26        Brooklyn            Manhattan Beach  40.577914 -73.943537     24   
27        Brooklyn                 Bath Beach  40.599519 -73.998752     33   
28        Brooklyn              Dyker Heights  40.619219 -74.019314     24   
29        Brooklyn               Clinton Hill  40.693229 -73.967843     36   
30        Brooklyn                   Downtown  40.690844 -73.983463     20   
31        Brooklyn  Prospect Lefferts Gardens  40.658420 -73.954899     31   
32        Brooklyn        Prospect Park South  40.647009 -73.962613     34   
33        Brooklyn          East Williamsburg  40.708492 -73.938858     20   
34        Brooklyn                 North Side  40.714823 -73.958809     26   
35        Brooklyn                 South Side  40.710861 -73.958001     29   
36        Brooklyn              Ocean Parkway  40.613060 -73.968367     25   
37        Brooklyn              Fort Hamilton  40.614768 -74.031979     25   
38       Manhattan                  Chinatown  40.715618 -73.994279     28   
39       Manhattan         Washington Heights  40.851903 -73.936900     35   
40       Manhattan                     Inwood  40.867684 -73.921210     30   
41       Manhattan           Hamilton Heights  40.823604 -73.949688     34   
42       Manhattan             Manhattanville  40.816934 -73.957385     34   
43       Manhattan             Central Harlem  40.815976 -73.943211     36   
44       Manhattan                East Harlem  40.792249 -73.944182     29   
45       Manhattan            Upper East Side  40.775639 -73.960508     26   
46       Manhattan                  Yorkville  40.775930 -73.947118     31   
47       Manhattan                 Lenox Hill  40.768113 -73.958860     29   
48       Manhattan           Roosevelt Island  40.762160 -73.949168     24   
49       Manhattan            Upper West Side  40.787658 -73.977059     33   
50       Manhattan               

### Untapped Markets

In [79]:
BM_merged[BM_merged['Total'] == 0].reset_index(drop=True)

Borough  Neighborhood   Latitude  Longitude  Total  Cluster_Labels
0          Bronx  Clason Point  40.806551 -73.854144      0               0
1  Staten Island     Todt Hill  40.597069 -74.111329      0               0
2  Staten Island    Port Ivory  40.639683 -74.174645      0               0
3  Staten Island     Rossville  40.549404 -74.215729      0               0
4  Staten Island    Bloomfield  40.605779 -74.187256      0               0

From this Data Analysis we can find that the neighborhoods in cluster 0 have fewer restaurants compared to that of the cluster 1 restaurants and are less saturated markets. There are 5 untapped markets i.e neighborhoods without any restaurants